In [ ]:
from netgen.occ import *
from ngsolve import *
from ngsolve.webgui import Draw

# Variable
E = 210000
nu = 0.3

# Dirichlet Boundaries
Face_Dirichletx = 'Face4'
Face_Dirichlety = 'Face4'
Face_Dirichletz = 'Face4'

# Loads parameter
FaceForce = 'Face2'
ForceVal = 200

# Degree of Element
EleDeg = 2

# Mesh the geometrie and get the boundaries --------------------------------------------------

# geo = OCCGeometry('Geometrie.stp')
box = Box((0,-10,-10), (200,10,10))
box.faces.Max(X).name="Face4"
box.faces.Min(X).name="Face2"
geo = OCCGeometry(box)

mesh = Mesh(geo.GenerateMesh(maxh=6)).Curve(3)
boundaries = list(mesh.GetBoundaries())

# Stress Function ----------------------------------------------------------------------------
mu  = E / 2 / (1+nu)
lam = E * nu / ((1+nu)*(1-2*nu))

def Stress(strain):
    return 2*mu*strain + lam*Trace(strain)*Id(3)

def thermal_stress(dt):
    global E, nu
    cT = 2e-6 * 2
    return -E * cT * dt / (1 - 2 * nu)

# FE Space ---------------------------------------------------------------------------------
fes = VectorH1(mesh, order=EleDeg, dirichletx=Face_Dirichletx, dirichlety=Face_Dirichlety, dirichletz=Face_Dirichletz)
u,v = fes.TnT()
gfu = GridFunction(fes)
dt = GridFunction(fes, "dt")

In [ ]:
# Assemble of a ----------------------------------------------------------------------------
with TaskManager():
    a = BilinearForm(InnerProduct(Stress(Sym(Grad(u))), Sym(Grad(v))).Compile()*dx)
    a += SymbolicEnergy(thermal_stress(dt) * u)
    dt.Set((-5e3 * x, -5e3 * y, -5e3 * z))  # I would like to make uniform temperature on all the beam, so I guess it is not like that.
    pre = Preconditioner(a, "bddc")
    a.AssembleLinearization(gfu.vec)
    # a.Assemble()

# Creation of the force value (applied on a face) -----------------------------------------
Dom = mesh.Boundaries(FaceForce)
area = Integrate(1, Dom)
print("Face Area : ", area)

Force_Value = ForceVal/area
force = CF((0, 0, Force_Value))

# f = LinearForm(force * v * ds(FaceForce)).Assemble()
f = LinearForm(fes).Assemble()

# Run the Solver --------------------------------------------------------------------------
from ngsolve.krylovspace import CGSolver
inv = CGSolver(a.mat, pre, printrates='\r', tol=1e-6, maxiter=500)
gfu.vec.data += inv * (f.vec - a.Apply(gfu.vec))

# Print Result --------------------------------------------------------------------------
with TaskManager():
    EFstress = MatrixValued(H1(mesh,order=EleDeg), symmetric=True)
    VMstress = GridFunction(EFstress)
    VMstress.Interpolate (Stress(Sym(Grad(gfu))))

In [ ]:
Draw (gfu)